In [15]:
import os
import re
import math
import json
from tqdm import tqdm
import random
from dotenv import load_dotenv
from huggingface_hub import login
import numpy as np
import pickle
from sentence_transformers import SentenceTransformer
from datasets import load_dataset
import chromadb
from items import Item
from sklearn.manifold import TSNE
import plotly.graph_objects as go

In [16]:
with open('train.pkl', 'rb') as file:
    train = pickle.load(file)

In [17]:
train[0].prompt

'How much does this cost to the nearest dollar?\n\nDelphi FG0166 Fuel Pump Module\nDelphi brings 80 years of OE Heritage into each Delphi pump, ensuring quality and fitment for each Delphi part. Part is validated, tested and matched to the right vehicle application Delphi brings 80 years of OE Heritage into each Delphi assembly, ensuring quality and fitment for each Delphi part Always be sure to check and clean fuel tank to avoid unnecessary returns Rigorous OE-testing ensures the pump can withstand extreme temperatures Brand Delphi, Fit Type Vehicle Specific Fit, Dimensions LxWxH 19.7 x 7.7 x 5.1 inches, Weight 2.2 Pounds, Auto Part Position Unknown, Operation Mode Mechanical, Manufacturer Delphi, Model FUEL PUMP, Dimensions 19.7\n\nPrice is $227.00'

In [18]:
DB = "products_vectorstore"

In [19]:
client = chromadb.PersistentClient(path=DB)

In [ ]:
# Check if the collection exists and delete it if it does
collection_name = "products"

# For old versions of Chroma, use this line instead of the subsequent one
# existing_collection_names = [collection.name for collection in client.list_collections()]
existing_collection_names = client.list_collections()

if collection_name in existing_collection_names:
    client.delete_collection(collection_name)
    print(f"Deleted existing collection: {collection_name}")

collection = client.create_collection(collection_name)


In [ ]:
model = SentenceTransformer('sentence-transformers/all-MiniLM-L6-v2')

In [21]:
vector = model.encode(["Well hi there"])[0]
vector

array([-9.46715921e-02,  4.27619852e-02,  5.51620908e-02, -5.10982354e-04,
        1.16203353e-02, -6.80130422e-02,  2.76406445e-02,  6.06974810e-02,
        2.88530681e-02, -1.74128301e-02, -4.94346023e-02,  2.30993200e-02,
       -1.28614539e-02, -4.31402288e-02,  2.17510201e-02,  4.26548794e-02,
        5.10500222e-02, -7.79727176e-02, -1.23247258e-01,  3.67455557e-02,
        4.54121176e-03,  9.47937518e-02, -5.53098992e-02,  1.70641821e-02,
       -2.92872526e-02, -4.47125323e-02,  2.06785351e-02,  6.39319792e-02,
        2.27427743e-02,  4.87789363e-02, -2.33508484e-03,  4.72859591e-02,
       -2.86258645e-02,  2.30625179e-02,  2.45130546e-02,  3.95680927e-02,
       -4.33176570e-02, -1.02316678e-01,  2.79876147e-03,  2.39304081e-02,
        1.61556378e-02, -8.99088103e-03,  2.07255036e-02,  6.40122816e-02,
        6.89178854e-02, -6.98361173e-02,  2.89762835e-03, -8.10989514e-02,
        1.71122309e-02,  2.50655250e-03, -1.06529057e-01, -4.87733409e-02,
       -1.67761575e-02, -

In [22]:
import numpy as np
def cosine_similarity(a, b):
    return np.dot(a, b) / (np.linalg.norm(a) * np.linalg.norm(b))

def how_similar(text1, text2):
    vector1, vector2 = model.encode([text1, text2])
    similarity = cosine_similarity(vector1, vector2)
    print(f"Similarity between {text1} and {text2} is {similarity*100:.1f}%")

In [23]:
how_similar("Java", "C++")
how_similar("Java", "mug")
how_similar("Cup of Java", "mug")

Similarity between Java and C++ is 50.7%
Similarity between Java and mug is 25.8%
Similarity between Cup of Java and mug is 49.3%


In [24]:
def description(item):
    text = item.prompt.replace("How much does this cost to the nearest dollar?\n\n", "")
    return text.split("\n\nPrice is $")[0]

In [25]:
description(train[0])

'Delphi FG0166 Fuel Pump Module\nDelphi brings 80 years of OE Heritage into each Delphi pump, ensuring quality and fitment for each Delphi part. Part is validated, tested and matched to the right vehicle application Delphi brings 80 years of OE Heritage into each Delphi assembly, ensuring quality and fitment for each Delphi part Always be sure to check and clean fuel tank to avoid unnecessary returns Rigorous OE-testing ensures the pump can withstand extreme temperatures Brand Delphi, Fit Type Vehicle Specific Fit, Dimensions LxWxH 19.7 x 7.7 x 5.1 inches, Weight 2.2 Pounds, Auto Part Position Unknown, Operation Mode Mechanical, Manufacturer Delphi, Model FUEL PUMP, Dimensions 19.7'

In [ ]:
NUMBER_OF_DOCUMENTS = len(train)

# Uncomment if you'd rather not wait for the full 400,000
# NUMBER_OF_DOCUMENTS = 20000

for i in tqdm(range(0, NUMBER_OF_DOCUMENTS, 1000)):
    documents = [description(item) for item in train[i: i+1000]]
    vectors = model.encode(documents).astype(float).tolist()
    metadatas = [{"category": item.category, "price": item.price} for item in train[i: i+1000]]
    ids = [f"doc_{j}" for j in range(i, i+len(documents))]
    collection.add(
        ids=ids,
        documents=documents,
        embeddings=vectors,
        metadatas=metadatas
    )